In [1]:
# 필요한 모듈과 라이브러리를 로딩
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
import pandas as pd
import time, os, math, random, sys, datetime
from datetime import date, timedelta, datetime
import pyautogui
from tqdm import tqdm

# chromedriver 자동 설치
import chromedriver_autoinstaller

from selenium.webdriver.common.action_chains import ActionChains


In [2]:
# 작업 시간과 고유 dir 등 생성
n = time.localtime()
s = '%04d-%02d-%02d' % (n.tm_year, n.tm_mon, n.tm_mday)
s_time = time.time( )


a = datetime.now()-timedelta(days=31)
a = a.strftime('%Y.%m.%d')
b = datetime.now()-timedelta(days=54)
b = b.strftime('%Y.%m.%d')
print(b, a)

2021.04.07 2021.04.30


In [3]:
print("=" *80)
print("         YOUTUBER 크롤러입니다.")
print("=" *80)

f_dir = os.path.expanduser('~') + f'\\Desktop\\crawler-bot\\COMMUNITY\\{b}-{a}\\' # 운영체제 상관없이 바탕화면 'crawler-bot' 폴더에 작업

print("=" *80)
print("데이터 크롤링을 시작합니다.")
print("=" *80)

         YOUTUBER 크롤러입니다.
데이터 크롤링을 시작합니다.


In [4]:
# 저장될 파일 경로와 이름을 지정
# 파일을 저장할 폴더 위치를 만들고, 중복일 경우 해당 폴더를 삭제하고 새로 생성합니다.
try : 
    os.makedirs(f_dir)
except : pass
else : 
    os.chdir(f_dir)

fc_name=f_dir+'\\'+f'youtube.csv'

In [5]:
# 크롤링 데이터가 들어갈 리스트 생성
domain2 = []    # 크롤링 도메인
title2 = []     # 게시물 제목
user2 = []      # 게시물 작성자
date2 = []     # 게시물 작성 시간
view2 = []     # 게시물 뷰 카운트

url2 = []      # 게시물 url
like2 = []     # 좋아요 - 싫어요
writer2 = []   # 댓글 작성자
com2 = []      # 댓글

In [6]:
# chromedriver-autoinstaller 이용
chromedriver_autoinstaller.install(cwd=True)

# HEADLESS MODE
options = webdriver.ChromeOptions()
# options.add_argument('headless')
options.add_argument('window-size=660,1080') 
# options.add_argument("--disable-gpu")
options.add_experimental_option('excludeSwitches', ['enable-logging'])
options.add_argument("user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_12_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/61.0.3163.100 Safari/537.36")
args = ["hide_console", ]

# 알림창 끄기
options.add_experimental_option("prefs", {"profile.default_content_setting_values.notifications": 1})

# 웹사이트 접속 후 해당 메뉴로 이동
driver = webdriver.Chrome(options=options,service_args=args)
# driver.maximize_window()

In [7]:
domain1 = "youtube"

In [8]:
url_list = [
    'https://www.youtube.com/c/%EB%94%B4%EC%A7%80%EB%B0%A9%EC%86%A1%EA%B5%AD/videos',
    'https://www.youtube.com/channel/UCu1FzjrHosuKGvgIx8oBi8w/videos',
    'https://www.youtube.com/c/%EC%9D%B4%EB%8F%99%ED%98%95TV/videos',
    'https://www.youtube.com/c/kimyongminTV/videos',
    'https://www.youtube.com/c/%EC%98%B3%EC%9D%80%EC%86%8C%EB%A6%AC/videos',
    'https://www.youtube.com/c/%EC%95%8C%EB%A6%AC%EB%AF%B8%ED%99%A9%ED%9D%AC%EB%91%90/videos',
    'https://www.youtube.com/channel/UCIMv9bOOGWGIfg6wPcRLItQ/videos'
]

# url2 = url_list

In [9]:
# 각 유튜브 페이지로 이동
for url in tqdm(url_list) :

    driver.get(url)
    driver.implicitly_wait(5)
    
    element = driver.find_element_by_tag_name('body')
    element.send_keys(Keys.END)
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_UP)
    time.sleep(random.randint(3,4))
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_DOWN)
    time.sleep(1)
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_UP)
    time.sleep(random.randint(3,4))
    element.send_keys(Keys.PAGE_DOWN)
    element.send_keys(Keys.PAGE_DOWN)
    
    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')    
    
    video_box = soup.find_all('ytd-grid-video-renderer')
    
    for video in video_box :
        video_url = f"https://www.youtube.com{video.find(name='a', attrs={'id':'thumbnail'})['href']}"
        
        driver.get(video_url)
        driver.implicitly_wait(5)        

        element = driver.find_element_by_tag_name('body')
        element.send_keys(Keys.END)
        element.send_keys(Keys.PAGE_DOWN)
        time.sleep(3.4)

        
        try :

            html = driver.page_source
            soup = BeautifulSoup(html, 'html.parser') 

            try :
                date1 = soup.find(name='div',attrs={'id':'info-text'}).find(name='div', attrs={'id':'date'}).find('yt-formatted-string').text.replace("최초 공개: ","").replace(" ","").replace("실시간스트리밍시작일:","").replace("이전실시간스트리밍:","")
            except :
                time.sleep(2)
                print(soup.find(name='div',attrs={'id':'info-text'}).find(name='div', attrs={'id':'date'}))
                date1 = soup.find(name='div', attrs={'id':'date'}).find('yt-formatted-string').text

            if "시간전" in date1 or "스트리밍시작" in date1:
                date1 = datetime.now().strftime('%Y.%m.%d').strip()
            else :
                date1 = date1[:-1].strip()

            if len(date1) != 10 :
    #             print("기존 1 :", date1)
                date1 = date1[:5] +"0" + date1[5:]
            if len(date1) != 10 :
    #             print("기존 2 :", date1)
                date1 = date1[:8] +"0" + date1[8:]      

            print("date :", date1)

            if date1 > a :
                pass
                print("\n")
                print("해당 게시물을 건너뜁니다.")
                print(video_url)
                print(a, "<",date1)     

            elif date1 >= b :
                print("\n")
                print("해당 게시물 댓글을 크롤링합니다.")
                print(video_url)
                print(b, "<=",date1)

                domain2.append(domain1)
                url2.append(video_url)

                html = driver.page_source
                soup = BeautifulSoup(html, 'html.parser')

                title1 = soup.find(name='h1', attrs={'class':'title style-scope ytd-video-primary-info-renderer'}).text.strip()
                print('title : ', title1)
                title2.append(title1)

                user1 = soup.find(name='div', attrs={'id':'text-container'}).text.strip()
                print("채널명 :", user1)
                user2.append(user1)

                date2.append(date1)

                black_box = soup.find_all(name='yt-formatted-string', attrs={'id':'text', 'class':'style-scope ytd-toggle-button-renderer style-text'})

                for box in black_box :
                    try :        
                        text = box['aria-label']
                        if "좋아요 " in text :
                            like1 = text.replace('좋아요 ', '').replace(',','').replace('개','').strip()
                        elif "싫어요 " in text :
                            dislike1 = text.replace('싫어요 ', '').replace(',','').replace('개','').strip()
                            break
                    except :
                        pass

                if like1 == "없음" :
                    like1 = 0
                if dislike1 == "없음" :
                    dislike1 = 0

                net_like = int(like1) - int(dislike1)
                print('net_like :', net_like)
                like2.append(net_like)

                element = driver.find_element_by_tag_name('body')
                element.send_keys(Keys.END)
                element.send_keys(Keys.PAGE_UP)
                element.send_keys(Keys.PAGE_DOWN)
                element.send_keys(Keys.PAGE_DOWN)
                element.send_keys(Keys.PAGE_DOWN)
                time.sleep(3)

                html = driver.page_source

                old_box = len(html)

                while True:

                    element.send_keys(Keys.PAGE_UP)
                    element.send_keys(Keys.PAGE_DOWN)
                    element.send_keys(Keys.PAGE_DOWN)
                    element.send_keys(Keys.PAGE_DOWN)
                    time.sleep(3)

                    html = driver.page_source

                    new_box = len(html)

                    print(new_box, old_box)

                    if new_box == old_box:
                        break
                    else :
    #                     print("스크롤을 내립니다.")
                        pass

                    old_box = new_box

                time.sleep(3)
                html = driver.page_source
                soup = BeautifulSoup(html, 'html.parser')

                comment_box = soup.find_all(name='div', attrs={'id':'contents'})[-1].find_all(name='ytd-comment-thread-renderer', attrs={'class':'style-scope ytd-item-section-renderer'})
                writers = []
                comments = []
                for comment in comment_box :       

                    try :
                        writer1 = comment.find(name='a', attrs={'id':'author-text'}).text.strip()
                        com1 = comment.find(name='yt-formatted-string', attrs={'id':'content-text'}).text.strip()
                        writers.append(writer1)
                        comments.append(com1)
                    except :
                        print("\n예외상황 :")
                        print(comment.text.strip().replace("\n", ""))

                print("댓글 작성자 :", writers)
                print(f"댓글 내용 :", comments)
                print("\n")

                writer2.append(writers)
                com2.append(comments)                 


            else :
                print("타겟 게시물이 아님")
                print(video_url)
                print(b, ">", date1)
                break
        except :
            time.sleep(3)
            
            html = driver.page_source
            soup = BeautifulSoup(html, 'html.parser') 

            try :
                date1 = soup.find(name='div',attrs={'id':'info-text'}).find(name='div', attrs={'id':'date'}).find('yt-formatted-string').text.replace("최초 공개: ","").replace(" ","").replace("실시간스트리밍시작일:","").replace("이전실시간스트리밍:","")
            except :
                time.sleep(2)
                print(soup.find(name='div',attrs={'id':'info-text'}).find(name='div', attrs={'id':'date'}))
                date1 = soup.find(name='div', attrs={'id':'date'}).find('yt-formatted-string').text

            if "시간전" in date1 or "스트리밍시작" in date1:
                date1 = datetime.now().strftime('%Y.%m.%d').strip()
            else :
                date1 = date1[:-1].strip()

            if len(date1) != 10 :
    #             print("기존 1 :", date1)
                date1 = date1[:5] +"0" + date1[5:]
            if len(date1) != 10 :
    #             print("기존 2 :", date1)
                date1 = date1[:8] +"0" + date1[8:]      

            print("date :", date1)

            if date1 > a :
                pass
                print("\n")
                print("해당 게시물을 건너뜁니다.")
                print(video_url)
                print(a, "<",date1)     

            elif date1 >= b :
                print("\n")
                print("해당 게시물 댓글을 크롤링합니다.")
                print(video_url)
                print(b, "<=",date1)

                domain2.append(domain1)
                url2.append(video_url)

                html = driver.page_source
                soup = BeautifulSoup(html, 'html.parser')

                title1 = soup.find(name='h1', attrs={'class':'title style-scope ytd-video-primary-info-renderer'}).text.strip()
                print('title : ', title1)
                title2.append(title1)

                user1 = soup.find(name='div', attrs={'id':'text-container'}).text.strip()
                print("채널명 :", user1)
                user2.append(user1)

                date2.append(date1)

                black_box = soup.find_all(name='yt-formatted-string', attrs={'id':'text', 'class':'style-scope ytd-toggle-button-renderer style-text'})

                for box in black_box :
                    try :        
                        text = box['aria-label']
                        if "좋아요 " in text :
                            like1 = text.replace('좋아요 ', '').replace(',','').replace('개','').strip()
                        elif "싫어요 " in text :
                            dislike1 = text.replace('싫어요 ', '').replace(',','').replace('개','').strip()
                            break
                    except :
                        pass

                if like1 == "없음" :
                    like1 = 0
                if dislike1 == "없음" :
                    dislike1 = 0

                net_like = int(like1) - int(dislike1)
                print('net_like :', net_like)
                like2.append(net_like)

                element = driver.find_element_by_tag_name('body')
                element.send_keys(Keys.END)
                element.send_keys(Keys.PAGE_UP)
                element.send_keys(Keys.PAGE_DOWN)
                element.send_keys(Keys.PAGE_DOWN)
                element.send_keys(Keys.PAGE_DOWN)
                time.sleep(3)

                html = driver.page_source

                old_box = len(html)

                while True:

                    element.send_keys(Keys.PAGE_UP)
                    element.send_keys(Keys.PAGE_DOWN)
                    element.send_keys(Keys.PAGE_DOWN)
                    element.send_keys(Keys.PAGE_DOWN)
                    time.sleep(3)

                    html = driver.page_source

                    new_box = len(html)

                    print(new_box, old_box)

                    if new_box == old_box:
                        break
                    else :
    #                     print("스크롤을 내립니다.")
                        pass

                    old_box = new_box

                time.sleep(3)
                html = driver.page_source
                soup = BeautifulSoup(html, 'html.parser')

                comment_box = soup.find_all(name='div', attrs={'id':'contents'})[-1].find_all(name='ytd-comment-thread-renderer', attrs={'class':'style-scope ytd-item-section-renderer'})
                writers = []
                comments = []
                for comment in comment_box :       

                    try :
                        writer1 = comment.find(name='a', attrs={'id':'author-text'}).text.strip()
                        com1 = comment.find(name='yt-formatted-string', attrs={'id':'content-text'}).text.strip()
                        writers.append(writer1)
                        comments.append(com1)
                    except :
                        print("\n예외상황 :")
                        print(comment.text.strip().replace("\n", ""))

                print("댓글 작성자 :", writers)
                print("댓글 길이 :", len(writers))
                print(f"댓글 내용 :", comments)
                print("\n")

                writer2.append(writers)
                com2.append(comments)                 


            else :
                print("타겟 게시물이 아님")
                print(video_url)
                print(b, ">", date1)
                break


  0%|                                                                                            | 0/7 [00:00<?, ?it/s]

date : 2021.05.28


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=enhWnNQubI8
2021.04.30 < 2021.05.28
date : 2021.05.28


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=3N52MYfgSTg
2021.04.30 < 2021.05.28
date : 2021.05.27


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=dokHKaBxi88
2021.04.30 < 2021.05.27
date : 2021.05.26


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=iWlPp6DE52M
2021.04.30 < 2021.05.26
date : 2021.05.21


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=-mpM4LgbwRY
2021.04.30 < 2021.05.21
date : 2021.05.19


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=FuGu3hANKj0
2021.04.30 < 2021.05.19
date : 2021.05.14


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=XC-qakHvvFU
2021.04.30 < 2021.05.14
date : 2021.05.12


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=719kBYg7a_4
2021.04.30 < 2021.05.12
date : 2021.05.07


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=9n0qM7br6JQ
2021.04.30 < 2021.05.07
date : 2021.05.05


해당 게시물을 건너뜁니다.
https://www.youtube.com/watch?v=pD2fbZ

date : 2021.04.30


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=MacDN3tcRGw
2021.04.07 <= 2021.04.30
title :  [김어준의 다스뵈이다] 160 : 싱어송라이터 정우
채널명 : 딴지방송국
net_like : 3495
4391689 4390001
4606547 4391689
4618520 4606547
4838603 4618520
4840522 4838603
5058329 4840522
5060011 5058329
5278637 5060011
5280329 5278637
5508711 5280329
5510179 5508711
5727728 5510179
5729290 5727728
5946602 5729290
5948414 5946602
6112550 5948414
6113448 6112550
6113448 6113448
댓글 작성자 : ['더함께민주당', '우동킬러', '윤창현', 'OR-KP', '몽이', '이준', 'Sluis Van', 'K Mr.', '트랑퀼라', '이준', 'Kevin Park', '괜찮아ok!', '박초밥', '평화둥이', '아이인', 'yonghyun lee', 'dooyeol Choi (Music travel) 음악 듣기용 공연 영상 및 연습 영상', '임선하', '어찌나좋은지', '김라니', '엄주영', '괜찮아ok!', '이현주', 'dooyeol Choi (Music travel) 음악 듣기용 공연 영상 및 연습 영상', '뚜르', '이현서', 'liberal values', '킹라이언', '박영미', 'M모리하', '김정순', '진형준', '수택김', 'Music List', 'Welt', '한블리', 'geospatial world', '고다르', 'dooyeol Choi (Music travel) 음악 듣기용 공연 영상 및 연습 영상', '괜찮아ok!', '정병인', '장성민', '노클라라', '채희관', '신주호', '스타

date : 2021.04.28


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=Ual3pWCtJMo
2021.04.07 <= 2021.04.28
title :  [지금 헤어지러 갑니다] ep.34 (우리 언니집인데)네가 왜 거기서 나와?
채널명 : 딴지방송국
net_like : 4771
4125199 4123504
4353472 4125199
4355054 4353472
4584853 4355054
4586917 4584853
4814883 4586917
4816670 4814883
5042477 4816670
5043928 5042477
5286113 5043928
5287260 5286113
5547824 5287260
5548950 5547824
5668947 5548950
5669724 5668947
5669724 5669724
댓글 작성자 : ['Kyung Su Kim', 'HG jeong', '차현주', '이유리', 'Eric', '밍밍', 'Sun _', 'mors sola', '우두커니', '박은영', '선미C', '보브', '빅피쉬', 'sun rain', '레알보수', 'chang', 'S.냥냥', '안개속삼겹살', '스톰트루퍼', 'SK Jeon', 'Mi jung Kim', '밍밍', '잭슨마이클', '신주호', '앤길버트', 'blue bird', '주현화', '임혜영', 'fantan can', 'Sky Yu', '밥국', 'Dododo Joo', 'KT kim', 'sh Phil', '쫄지마', '떡락', 'Inner peace', '최혁', '1分리뷰', 'Snowphia Kim', 'Fiorentina Choi', 'sunwoo kim', 'HYUNSUK JO', '최미애', 'nice great', 'Jonghak Lee', '구에스더', 'lee Zack', '조택96', '최선호', '조성오 튜브', '반짝반짝', 'dk s', '장민자', '신의두수', '어부', 'ho ho

date : 2021.04.23


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=Sx0kFL-yQug
2021.04.07 <= 2021.04.23
title :  김어준의 다스뵈이다 159회 유시민의 세월, 최배근의 망고, 조국의 폴더
채널명 : 딴지방송국
net_like : 72526
4404156 4403054
4658980 4404156
4660103 4658980
4911892 4660103
4913397 4911892
5150125 4913397
5152333 5150125
5375710 5152333
5377382 5375710
5613822 5377382
5615193 5613822
5851608 5615193
5853077 5851608
6075975 5853077
6077668 6075975
6306208 6077668
6307553 6306208
6542315 6307553
6543849 6542315
6777819 6543849
6779618 6777819
7003880 6779618
7003756 7003880
7233014 7003756
7234463 7233014
7453514 7234463
7455111 7453514
7673627 7455111
7675201 7673627
7902801 7675201
7904456 7902801
8127956 7904456
8129643 8127956
8365023 8129643
8366706 8365023
8596076 8366706
8597973 8596076
8815473 8597973
8817264 8815473
9043774 8817264
9045582 9043774
9268947 9045582
9270512 9268947
9489226 9270512
9490901 9489226
9697921 9490901
9710442 9697921
9899459 9710442
9932991 9899459
10160665 9932991
10162105 101

...

date : 2021.04.09


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=8fwPmzIyk2M
2021.04.07 <= 2021.04.09
title :  #140 선거기간 언론행태, 정말 빡친다! 초선 2030 왜 이러나!
채널명 : 박시영TV
net_like : 9743
4134811 4133260
4375078 4134811
4376528 4375078
4610458 4376528
4611822 4610458
4828387 4611822
4829724 4828387
5058771 4829724
5060450 5058771
5278987 5060450
5280434 5278987
5508927 5280434
5510504 5508927
5728758 5510504
5730309 5728758
5948265 5730309
5949918 5948265
6171795 5949918
6173027 6171795
6408850 6173027
6410213 6408850
6642699 6410213
6643802 6642699
6865416 6643802
6866860 6865416
7096685 6866860
7097939 7096685
7326370 7097939
7327705 7326370
7555037 7327705
7556370 7555037
7812423 7556370
7813639 7812423
8047182 7813639
8048403 8047182
8280705 8048403
8282028 8280705
8513591 8282028
8514928 8513591
8642828 8514928
8643392 8642828
8643513 8643392
8643513 8643513
댓글 작성자 : ['야인', 'Yenny S', '구절초세진', '박미자', '먹튀', 'Yenny S', 'yongs choi', 'Julio CHO', 'boy tom', '이원자', '이준식', 'Inho Lee', 'Oh보

date : 2021.04.08


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=_5npC5wNYtI
2021.04.07 <= 2021.04.08
title :  #139 민주당 지도부가 2030 마음을 얻으려면...
채널명 : 박시영TV
net_like : 7719
4162558 4161070
4389746 4162558
4391097 4389746
4624380 4391097
4625833 4624380
4849319 4625833
4850969 4849319
5078956 4850969
5080398 5078956
5303805 5080398
5305143 5303805
5534744 5305143
5535948 5534744
5778365 5535948
5779704 5778365
6006115 5779704
6007654 6006115
6241458 6007654
6242479 6241458
6485328 6242479
6486329 6485328
6725645 6486329
6726784 6725645
6965686 6726784
6967030 6965686
7199900 6967030
7201135 7199900
7452967 7201135
7454203 7452967
7693274 7454203
7694608 7693274
7936234 7694608
7937576 7936234
8191387 7937576
8192626 8191387
8437430 8192626
8438663 8437430
8639499 8438663
8702226 8639499
8702899 8702226
8702899 8702899
댓글 작성자 : ['미루', '보실', '준건이형', 'sp k', '김진태', 'Nicole hwang', '지재근', '샤인디케이', 'John Park', '지산심해', 'Alone Among', '초이스기백', '롤리팝', '이승준', '김정윤', '문동렬', '135 swan', '장브레송'

date : 2021.04.07


해당 게시물 댓글을 크롤링합니다.
https://www.youtube.com/watch?v=IxiE_kI0TnI
2021.04.07 <= 2021.04.07
title :  [특집생방송] 4.7재보선 개표방송 LIVE “어게인 박시영의폰”
채널명 : 박시영TV
net_like : 12666
4122616 4121485
4371002 4122616
4372460 4371002
4622322 4372460
4623760 4622322
4867205 4623760
4863732 4867205
5110533 4863732
5111882 5110533
5378969 5111882
5380226 5378969
5620941 5380226
5622169 5620941
5875598 5622169
5876806 5875598
6129859 5876806
6130975 6129859
6379838 6130975
6381075 6379838
6651193 6381075
6652301 6651193
6927137 6652301
6928135 6927137
7004809 6928135
7004924 7004809
7004924 7004924
댓글 작성자 : ['김정윤', '민족정기', 'free rider love', '김다현', '미루', 'ᄋᄋ', 'mors sola', 'Kevin Kim', '건강족구', '선우의팽이공장', '문찌방', '135 swan', 'Youngil Kwon', '바람', '김다현', '이노센스', '꼭두새벽', 'hwa b', '날라 Nalra', 'Il Sik Jeon', '한미완의꿈', 'sky888sky888 sky', 'AHNwood', 'scope 2020', '창맘', 'AZ백신1차접종완료', '펭러뷰', '나무꾼', '이경희', 'JD Kang', '박혜숙', '가을겨울', 'peele jung', 'kendrick.S', '정데레사', '민족정기', '박성희', '수아씨', 'Xianlu Yi', '

100%|████████████████████████████████████████████████████████████████████████████████| 7/7 [3:15:12<00:00, 1673.20s/it]

date : 2021.04.06
타겟 게시물이 아님
https://www.youtube.com/watch?v=x81f8ONiMPw
2021.04.07 > 2021.04.06


In [10]:
df = pd.DataFrame()

df['domain'] = pd.Series(domain2)
df['title'] = pd.Series(title2)
df['channel'] = pd.Series(user2)
df['date'] = pd.Series(date2)
df['url'] = pd.Series(url2)
df['like'] = pd.Series(like2)
df['commentor'] = pd.Series(writer2)
df['comment'] = pd.Series(com2)

df

domain                                           title channel  \
0   youtube          김어준의 다스뵈이다 160회 비트코인, 표창장 사기극, 역주행 고정운   딴지방송국   
1   youtube                    [김어준의 다스뵈이다] 160 : 싱어송라이터 정우   딴지방송국   
2   youtube      [지금 헤어지러 갑니다] ep.34 (우리 언니집인데)네가 왜 거기서 나와?   딴지방송국   
3   youtube        김어준의 다스뵈이다 159회 유시민의 세월, 최배근의 망고, 조국의 폴더   딴지방송국   
4   youtube     [지금 헤어지러 갑니다] ep.33 남편은 업소에서 살아. 나는 이혼할 거야.   딴지방송국   
..      ...                                             ...     ...   
85  youtube  #142 '야당협치' 주장은, 국민의힘 프레임! #미디어바우처, 언론개혁의 묘수다!   박시영TV   
86  youtube          #141 정경심 재판, 희망이 보인다! 김영배, 최고위원 도전 이유!   박시영TV   
87  youtube          #140 선거기간 언론행태, 정말 빡친다! 초선 2030 왜 이러나!   박시영TV   
88  youtube                  #139 민주당 지도부가 2030 마음을 얻으려면...   박시영TV   
89  youtube            [특집생방송] 4.7재보선 개표방송 LIVE “어게인 박시영의폰”   박시영TV   

          date                                          url   like  \
0   2021.04.30  https://www.youtube.com/watch?v=xYqSBNc_RZs  57165   
1   2021.04.30  https://www.youtube.com/watch?v=MacDN3tcRGw   3495   
2   2021.04.28  https://www.youtube.com/watch?v=Ual3pWCtJMo   4771   
3   2021.04.23  https://www.youtube.com/watch?v=Sx0kFL-yQug  72526   
4   2021.04.21  https://www.youtube.com/watch?v=Ak26RtSWrfs   4783   
..         ...                                          ...    ...   
85  2021.04.15  https://www.youtube.com/watch?v=LXI4ILJ0Qwk   7343   
86  2021.04.14  https://www.youtube.com/watch?v=OUYp_3ga3_s   6496   
87  2021.04.09  https://www.youtube.com/watch?v=8fwPmzIyk2M   9743   
88  2021.04.08  https://www.youtube.com/watch?v=_5npC5wNYtI   7719   
89  2021.04.07  https://www.youtube.com/watch?v=IxiE_kI0TnI  12666   

                                            commentor  \
0   [조영애, 남동운, 이유니크, Eunice Han, mm m, Mike Chue, ...   
1   [더함께민주당, 우동킬러, 윤창현, OR-KP, 몽이, 이준, Sluis Van, ...   
2   [Kyung Su Kim, HG jeong, 차현주, 이유리, Eric, 밍밍, S...   
3   [시사 경제 탐구티비, 절개완, SY Lee, 설탕초코, Eric Lee, frap...   
4   [김근우, Fund Bae, HJ K, J Godzila, 이대수, LubbockT...   
..                                                ...   
85  [김선화., Aila Westie, 최신지, donghoon lee, Leeᄋᄋᄋ,...   
86  [임지아, fdsaghh sg, 한빛, 유성목, Cho Kevin, 미래예 언, H...   
87  [야인, Yenny S, 구절초세진, 박미자, 먹튀, Yenny S, yongs c...   
88  [미루, 보실, 준건이형, sp k, 김진태, Nicole hwang, 지재근, 샤...   
89  [김정윤, 민족정기, free rider love, 김다현, 미루, ᄋᄋ, mors...   

                                              comment  
0   [휴가여서쉬시는줄알았는데..\nㅋㅋ..\n보너스같네요.\n총수님사랑합니다., 표창장...  
1   [뉴공에 나왔던 \n뉴공을 듣는 버스기사님을 위해 노래를 부르신 정우님이 군요~~ㅎ...  
2   [예전에 "사랑과 전쟁"의 배우가 했던말이.."저희 드라마를 막장드라마라고 욕하시는...  
3   [어준이가 엄청 강한 것 같아도 마음이 아주 여리거든...\n요즘 많이 얻어 맞으니...  
4   [아내의 대응방식에도 문제가 있다고 봅니다 농담으로라도 부부인데 그냥 밖에서 해결하...  
..                                                ...  
85  [국민의명령이다 모두개혁하라\n검찰개혁 언론개혁 사법개혁 재벌개혁 사학개혁 종교개혁...  
86  [고일석 기자가 정확하다\n이낙연이 된 이후로 무능해졌다, 정경심교수님   재판은 ...  
87  [민생경제 안소장님 같은분들이 국회에서 일을하면 참 잘하실것 같아요 ~, 초선이니 ...  
88  [몸 안에서 무엇인가 무너져 내린 기분..\n그래도 힘내고 가야죠\n민주당은 뼈아픈...  
89  [민주당 이번 패배에서 마니 배워라. \n박시영 김용민. 이동형 김종배 하는이야기 ...  

[90 rows x 8 columns]

In [11]:
target = []
re_url = []
for i in range(len(df)) :
    if len(df['commentor'][i]) < 1 :
        target.append(i)
        re_url.append(df['url'][i])
        
# 댓글 리크롤링

new_writer2 = []
new_com2 = []

for url in tqdm(re_url) :
    
    print("URL : ", url)

    driver.get(url)
    driver.implicitly_wait(5)
    time.sleep(3)
    element = driver.find_element_by_tag_name('body')
    element.send_keys(Keys.END)
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight-50);")
    time.sleep(5)

    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')

    old_box = len(html)

    while True:

        element = driver.find_element_by_tag_name('body')
        element.send_keys(Keys.END)
        html = driver.page_source
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight-3);")
        time.sleep(3)

        new_box = len(html)

        print(new_box, old_box)

        if new_box == old_box:
            break

        old_box = new_box

    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')

    comment_box = soup.find(name='div', attrs={'id':'contents'}).find_all(name='ytd-comment-thread-renderer', attrs={'class':'style-scope ytd-item-section-renderer'})
    writers = []
    comments = []
    for comment in comment_box :
        

        try :
            writer1 = comment.find(name='a', attrs={'id':'author-text'}).text.strip()
            com1 = comment.find(name='yt-formatted-string', attrs={'id':'content-text'}).text.strip()
            writers.append(writer1)
            comments.append(com1)
        except :
            print("\n예외상황 :")
            print(comment.text.strip().replace("\n", ""))
            
    print("댓글 작성자 :", writers)
    print(f"댓글 내용 :", comments)
    print("\n")
    
    new_writer2.append(writers)
    new_com2.append(comments)
    
for i in range(len(target)) :
    df['commentor'][target[i]] = new_writer2[i]
    df['comment'][target[i]] = new_com2[i]

# print(df[df['commentor'] == []])
df

0it [00:00, ?it/s]


domain                                           title channel  \
0   youtube          김어준의 다스뵈이다 160회 비트코인, 표창장 사기극, 역주행 고정운   딴지방송국   
1   youtube                    [김어준의 다스뵈이다] 160 : 싱어송라이터 정우   딴지방송국   
2   youtube      [지금 헤어지러 갑니다] ep.34 (우리 언니집인데)네가 왜 거기서 나와?   딴지방송국   
3   youtube        김어준의 다스뵈이다 159회 유시민의 세월, 최배근의 망고, 조국의 폴더   딴지방송국   
4   youtube     [지금 헤어지러 갑니다] ep.33 남편은 업소에서 살아. 나는 이혼할 거야.   딴지방송국   
..      ...                                             ...     ...   
85  youtube  #142 '야당협치' 주장은, 국민의힘 프레임! #미디어바우처, 언론개혁의 묘수다!   박시영TV   
86  youtube          #141 정경심 재판, 희망이 보인다! 김영배, 최고위원 도전 이유!   박시영TV   
87  youtube          #140 선거기간 언론행태, 정말 빡친다! 초선 2030 왜 이러나!   박시영TV   
88  youtube                  #139 민주당 지도부가 2030 마음을 얻으려면...   박시영TV   
89  youtube            [특집생방송] 4.7재보선 개표방송 LIVE “어게인 박시영의폰”   박시영TV   

          date                                          url   like  \
0   2021.04.30  https://www.youtube.com/watch?v=xYqSBNc_RZs  57165   
1   2021.04.30  https://www.youtube.com/watch?v=MacDN3tcRGw   3495   
2   2021.04.28  https://www.youtube.com/watch?v=Ual3pWCtJMo   4771   
3   2021.04.23  https://www.youtube.com/watch?v=Sx0kFL-yQug  72526   
4   2021.04.21  https://www.youtube.com/watch?v=Ak26RtSWrfs   4783   
..         ...                                          ...    ...   
85  2021.04.15  https://www.youtube.com/watch?v=LXI4ILJ0Qwk   7343   
86  2021.04.14  https://www.youtube.com/watch?v=OUYp_3ga3_s   6496   
87  2021.04.09  https://www.youtube.com/watch?v=8fwPmzIyk2M   9743   
88  2021.04.08  https://www.youtube.com/watch?v=_5npC5wNYtI   7719   
89  2021.04.07  https://www.youtube.com/watch?v=IxiE_kI0TnI  12666   

                                            commentor  \
0   [조영애, 남동운, 이유니크, Eunice Han, mm m, Mike Chue, ...   
1   [더함께민주당, 우동킬러, 윤창현, OR-KP, 몽이, 이준, Sluis Van, ...   
2   [Kyung Su Kim, HG jeong, 차현주, 이유리, Eric, 밍밍, S...   
3   [시사 경제 탐구티비, 절개완, SY Lee, 설탕초코, Eric Lee, frap...   
4   [김근우, Fund Bae, HJ K, J Godzila, 이대수, LubbockT...   
..                                                ...   
85  [김선화., Aila Westie, 최신지, donghoon lee, Leeᄋᄋᄋ,...   
86  [임지아, fdsaghh sg, 한빛, 유성목, Cho Kevin, 미래예 언, H...   
87  [야인, Yenny S, 구절초세진, 박미자, 먹튀, Yenny S, yongs c...   
88  [미루, 보실, 준건이형, sp k, 김진태, Nicole hwang, 지재근, 샤...   
89  [김정윤, 민족정기, free rider love, 김다현, 미루, ᄋᄋ, mors...   

                                              comment  
0   [휴가여서쉬시는줄알았는데..\nㅋㅋ..\n보너스같네요.\n총수님사랑합니다., 표창장...  
1   [뉴공에 나왔던 \n뉴공을 듣는 버스기사님을 위해 노래를 부르신 정우님이 군요~~ㅎ...  
2   [예전에 "사랑과 전쟁"의 배우가 했던말이.."저희 드라마를 막장드라마라고 욕하시는...  
3   [어준이가 엄청 강한 것 같아도 마음이 아주 여리거든...\n요즘 많이 얻어 맞으니...  
4   [아내의 대응방식에도 문제가 있다고 봅니다 농담으로라도 부부인데 그냥 밖에서 해결하...  
..                                                ...  
85  [국민의명령이다 모두개혁하라\n검찰개혁 언론개혁 사법개혁 재벌개혁 사학개혁 종교개혁...  
86  [고일석 기자가 정확하다\n이낙연이 된 이후로 무능해졌다, 정경심교수님   재판은 ...  
87  [민생경제 안소장님 같은분들이 국회에서 일을하면 참 잘하실것 같아요 ~, 초선이니 ...  
88  [몸 안에서 무엇인가 무너져 내린 기분..\n그래도 힘내고 가야죠\n민주당은 뼈아픈...  
89  [민주당 이번 패배에서 마니 배워라. \n박시영 김용민. 이동형 김종배 하는이야기 ...  

[90 rows x 8 columns]

In [12]:
# csv 형태로 저장하기
df.to_csv(fc_name,encoding="utf-8-sig",index=False)

e_time = time.time( )
t_time = e_time - s_time

print("\n")
print("=" *80)
print("1.총 소요시간은 %s 초 입니다 " %round(t_time,1))
print("2.파일 저장 완료: csv 파일명 : %s " %fc_name)

driver.quit()
sys.exit("프로그램을 종료합니다.")



1.총 소요시간은 11715.2 초 입니다 
2.파일 저장 완료: csv 파일명 : C:\Users\JPARK-02\Desktop\crawler-bot\COMMUNITY\2021.04.07-2021.04.30\\youtube.csv 
